In [ ]:
---
title: 1D string vibration (2D) - part I
description: Separation of variables
author: Daning H.
show-code: False
show-prompt: False
params:
    c:
        input: numeric
        label: Wave speed
        value: 1.0
        step: 1.0
    dmp:
        input: numeric
        label: Damping
        value: 0.0
        step: 0.1
---

**The 2D version**

We solve a 1D string vibration problem with fixed ends on the domain $0\leq x\leq \pi,\, t\geq 0$
$$
\begin{aligned}
&\, u_{tt} = c^2u_{xx} \\
&\, u(0,t) = 0,\quad u(\pi,t) = 0, \\
&\, u(x,0)=f(x),\quad u_t(x,0)=0
\end{aligned}
$$
where $c$ is the **wave speed** and see figure below for the definition of initial displacement $f(x)$.  The initial velocity is assumed to be zero.

Here we solve the problem by **separation of variables**, and the series solution is,
$$
u(x,t) = \sum_{n=1}^\infty u_n(x,t) = \sum_{n=1}^\infty \cos(nct)\sin(nx)
$$
where $u_n(x,t)$ are the eigenfunctions ("modes").  The **spatial modes** $\sin(nx)$ oscillate with a period $2\pi/(nc)$.  In the figures we plot the entire series solution, as well as the first three eigenfunctions.

When interacting with the different solutions, think about:
+ What is the effect of $c$?  Why do we call it wave speed?
+ We also implemented a "damped" solution, where higher order modes decay over time.  Physically what does it mean?

In [17]:
dmp = 0.0
c = 1.0

In [18]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np

def oddExt(f, P):
    def _fOdd(x):
        _x0 = np.array(x)
        _y  = np.zeros_like(_x0)
        _x  = np.mod(_x0, 2*P)
        _m  = _x <= P
        _y[_m] = f(_x[_m])
        _y[~_m] = -f(2*P-_x[~_m])
        return _y
    return _fOdd

def solk(x, t, k):
    _u = np.zeros((k, x.shape[0]))
    for _i in range(k):
        _n = 2*_i+1
        _c = 0.8/(np.pi*_n**3)
        _u[_i] = _c * np.cos(_n*c*t) * np.sin(_n*x) * np.exp(-dmp*_i*t)
    return _u

bnd = np.pi
nT  = 2   # Number of periods
Nx  = 101
Nt  = 51*nT
xlm = 0.3

fd = lambda x: 0.1*x*(bnd-x)
od = oddExt(fd, bnd)

# Solutions
## D'Alembert sol'n, exact
x  = np.linspace(-2*bnd, 3*bnd, Nx)
x0 = np.linspace(0.0, bnd, Nx)
t  = np.linspace(0.0, 2*nT*bnd/c, Nt)
X, T = np.meshgrid(x, t)
X0, T0 = np.meshgrid(x0, t)
f1 = 0.5*od(X-c*T)
f2 = 0.5*od(X+c*T)
fs = 0.5*od(X0-c*T0) + 0.5*od(X0+c*T0)

## SoV
Nmod = 5
Nplt = 3
dat  = np.zeros((Nt, Nmod, Nx))
for _i in range(Nt):
    dat[_i] = solk(x0, t[_i], Nmod)
sol = np.sum(dat, axis=1)

# Make the plots
fig = make_subplots(rows=1+Nplt, cols=1,
                    shared_xaxes=True, vertical_spacing=0.05,
                    subplot_titles=("Series solution", ) + \
                    tuple([f"Mode {_i}, Freq={c/(2*_i-1):4.3f}" for _i in range(1,Nplt+1)]))

# Add traces
## Initial conditions and final solution on both plots
fig.add_trace(go.Scatter(
    visible=True, line=dict(color="black", width=1), mode='lines',
    name="Initial cond.", x=x0, y=fs[0]), row=1, col=1)
for _i in range(Nplt):
    fig.add_trace(go.Scatter(
        visible=True, line=dict(color="black", width=1), mode='lines',
        showlegend=False, x=x0, y=dat[0,_i]), row=_i+2, col=1)

## Full solution
for _i in range(Nt):
    fig.add_trace(
        go.Scatter(
            visible=False, line=dict(color="blue", width=2),
            name="Response", x=x0, y=fs[_i]), row=1, col=1)
for _i in range(Nt):
    fig.add_trace(
        go.Scatter(
            visible=False, line=dict(color="red", width=2, dash='dash'),
            name="SoV solution", x=x0, y=sol[_i]), row=1, col=1)

## Mode decomposition
for _j in range(Nplt):
    for _i in range(Nt):
        fig.add_trace(
            go.Scatter(
                visible=False, line=dict(color='black', width=2),
                showlegend=False, x=x0, y=dat[_i,_j]), row=_j+2, col=1)

## Initial visibility
offset = 1+Nplt
for _j in range(Nplt+2):
    fig.data[_j*Nt+offset].visible = True

# Create and add slider
steps = []
for _i in range(Nt):
    step = dict(
        method="update",
        args=[{"visible": [True]*offset + [False] * (Nt*(Nplt+2))}],
        label=f"{_i*nT/(Nt-1.0):3.2f} T"
    )
    for _j in range(Nplt+2):
        step["args"][0]["visible"][_j*Nt+_i+offset] = True
    steps.append(step)

sliders = [dict(
    active=0,
    currentvalue={"prefix": "t = "},
    pad={"t": 50},
    steps=steps
)]

fig.update_layout(
    sliders=sliders,
    autosize=False,
    width=800,
    height=800)

rng = np.pi**2/4*0.1 * 1.1
fig.update_yaxes(title_text="y", range=[-rng,rng], row=1, col=1)
for i in range(Nplt):
    rng = np.max(dat[:,i]) * 1.1
    fig.update_yaxes(title_text="y", range=[-rng,rng], row=i+2, col=1)
for i in range(1+Nplt):
    fig.update_xaxes(tickvals = [0, np.pi/2, np.pi], row=i+1, col=1)
fig.update_xaxes(title_text="x",
                 ticktext = ['$0$', '$\pi/2$', '$\pi$'],
                 row=4, col=1)

fig.show()